In [1]:
import praw
import pandas as pd
import re
import string
import emoji as e
import logging
import scattertext as st
import nltk

from sklearn import datasets
from sklearn.feature_extraction import text 
from sklearn.decomposition import TruncatedSVD,NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
from nltk.tokenize import MWETokenizer, word_tokenize
from nltk import pos_tag
from gensim import corpora, models, matutils

from nltk.stem import WordNetLemmatizer, LancasterStemmer



# Reddit Scrape

This is just a sample of how I scraped each subReddit for each post category (hot, new, rising, top), then formatted my data in a Pandas dataframe.

In [ ]:
#setup reddit client
user_agent = # insert user agent here
reddit = praw.Reddit(
    client_id = # insert client id here,
    client_secret = # insert client secret here,
    user_agent = user_agent
)

In [3]:
title = []
ID = []
author = []
created_utc = []
score = []
upvote_ratio = []
url = []
selftext = []
name = []
num_comments = []
for submission in reddit.subreddit('aspergirls').hot(limit=1000):
    title.append(submission.title)
    ID.append(submission.id)
    author.append(submission.author)
    created_utc.append(submission.created_utc)
    score.append(submission.score)
    upvote_ratio.append(submission.upvote_ratio)
    url.append(submission.url)
    selftext.append(submission.selftext)
    name.append(submission.name)
    num_comments.append(submission.num_comments)

In [4]:
# Create a dataframe from zipped lists. Pickle for later.
zippedList =  list(zip(ID,title,author,created_utc,score,upvote_ratio,selftext,name,num_comments)) 
df = pd.DataFrame(zippedList,
                     columns = ['ID','title','author','created_utc','score','upvote_ratio','selftext','name','num_comments']) 
df.to_pickle('aspergirls_hot_0507.pkl')
df.shape

(957, 9)

In [5]:
df.sample(10)

ID                                              title  \
641  u4y9ji  what are some of your social interactions that...   
204  ug23ix  I'm Within a Period of Self-Realization & Intr...   
630  u5q11j                     I started a YouTube channel...   
315  ud6pff  Adjustments that have helped you avoid/mitigat...   
189  ufy73p  Messed up by asking someone not that close to ...   
243  uf8gcv  How to find structure after high school finish...   
684  u4k50a  how to succeed panel interview for a software ...   
104  uiagb4             Does context matter for "How are you"?   
720  u2uhb4  I just need some emotional support. I’m having...   
302  ue1auk       what could lead doctors to not diagnose you?   

                   author   created_utc  score  upvote_ratio  \
641              petpuppy  1.650117e+09    115          1.00   
204   OfficialThrowaway_1  1.651418e+09     15          0.86   
630              mayg3588  1.650211e+09     23          0.93   
315             Paulakris  1.651075e+09     72          0.99   
189   borderlineintrovert  1.651406e+09    242          0.96   
243           domeofgnome  1.651315e+09     10          1.00   
684    findmeinthe_future  1.650064e+09      1          1.00   
104               Talvana  1.651682e+09      9          0.92   
720  SimonSaysGetRichBtch  1.649868e+09     16          0.95   
302          princesiddie  1.651169e+09      5          0.86   

                                              selftext       name  \
641  so obviously its no rare occasion for any of u...  t3_u4y9ji   
204  (TL;DR:Writing a bit of a journal entry I gues...  t3_ug23ix   
630  Feeling low and unsure about myself this morni...  t3_u5q11j   
315  So I remember someone recently posting about t...  t3_ud6pff   
189                                                     t3_ufy73p   
243   \n\nHi there! So, I recently finished high sc...  t3_uf8gcv   
684  Hello! I got an interview, bad news is that it...  t3_u4k50a   
104  Where I live, "How are you" is basically just ...  t3_uiagb4   
720  Title sums it up. I’m currently stranded on th...  t3_u2uhb4   
302  i was tested for autism among other things abo...  t3_ue1auk   

     num_comments  
641            79  
204             7  
630            17  
315            56  
189            47  
243             7  
684             0  
104            22  
720            10  
302             3

# Data Cleaning and EDA

In [6]:
# Read in all pickled files
aspergirls_1 = pd.read_pickle('aspergirls_hot_0504.pkl')
aspergirls_2 = pd.read_pickle('aspergirls_new_0504.pkl')
aspergirls_3 = pd.read_pickle('aspergirls_rising_0504.pkl')
aspergirls_4 = pd.read_pickle('aspergirls_top_0504.pkl')
AutismInWomen_1 = pd.read_pickle('AutismInWomen_hot_0504.pkl')
AutismInWomen_2 = pd.read_pickle('AutismInWomen_new_0504.pkl')
AutismInWomen_3 = pd.read_pickle('AutismInWomen_rising_0504.pkl')
AutismInWomen_4 = pd.read_pickle('AutismInWomen_top_0504.pkl')

autism_1 = pd.read_pickle('autism_hot_0504.pkl')
autism_2 = pd.read_pickle('autism_new_0504.pkl')
autism_3 = pd.read_pickle('autism_rising_0504.pkl')
autism_4 = pd.read_pickle('autism_top_0504.pkl')
aspergers_1 = pd.read_pickle('aspergers_hot_0504.pkl')
aspergers_2 = pd.read_pickle('aspergers_new_0504.pkl')
aspergers_3 = pd.read_pickle('aspergers_rising_0504.pkl')
aspergers_4 = pd.read_pickle('aspergers_top_0504.pkl')


In [7]:
autism_fem = pd.concat([aspergirls_1, aspergirls_2, aspergirls_3, aspergirls_4,
                       AutismInWomen_1, AutismInWomen_2, AutismInWomen_3, AutismInWomen_4]).drop_duplicates(subset='title').reset_index(drop=True)
autism_gen = pd.concat([autism_1, autism_2, autism_3, autism_4, 
                        aspergers_1, aspergers_2, aspergers_3, aspergers_4]).drop_duplicates(subset='title').reset_index(drop=True)
autism_total = pd.concat([aspergirls_1, aspergirls_2, aspergirls_3, aspergirls_4,
                       AutismInWomen_1, AutismInWomen_2, AutismInWomen_3, AutismInWomen_4,
                         autism_1, autism_2, autism_3, autism_4, 
                        aspergers_1, aspergers_2, aspergers_3, aspergers_4]).drop_duplicates(subset='title').reset_index(drop=True)

autism_fem.shape, autism_gen.shape, autism_total.shape

((3816, 9), (3977, 9), (7776, 9))

In [8]:
autism_fem.title[20]
autism_gen[autism_gen.title == 'does anyone else get fomo from podcasts ']

Empty DataFrame
Columns: [ID, title, author, created_utc, score, upvote_ratio, selftext, name, num_comments]
Index: []

In [9]:
# Convert unix timestamp to datetime. Make sure title and selftext columns are in str format.
autism_fem['created_utc'] = pd.to_datetime(autism_fem['created_utc'], unit='s')
autism_fem['title'] = autism_fem['title'].astype(str)
autism_fem['selftext'] = autism_fem['selftext'].astype(str)

autism_gen['created_utc'] = pd.to_datetime(autism_gen['created_utc'], unit='s')
autism_gen['title'] = autism_gen['title'].astype(str)
autism_gen['selftext'] = autism_gen['selftext'].astype(str)


In [10]:
# Take a look at the corpus before pre-processing
corpus_origin = list(autism_fem.title + ' ' + autism_fem.selftext)
corpus_origin

['Origin Story Megathread We get a lot of foot traffic from people who are in the process of discovering, investigating, and considering an autism diagnosis. This is a very turbulent time and people going through this discovery process want to know if they are on the right track. Unfortunately, we are not medical professionals and we cannot give any advice on what individual people should or should not do. However, those of us who have gone through this process can still help by sharing our experience with it. Hopefully the new people will see a story in the comments that they resonate with. So, please, tell us your origin story. Regale us with tales of how you discovered the world\'s most unusual "superpower".\n\nQuestions we see lot are: \n\n1) How did you first learn about the way autism presents in girls?  \n2) When did you realize you fit on the spectrum?  \n3) What made you realize you were autistic?  \n4) Is going after a diagnosis worth it?  \n5) What is the diagnosis process l

In [11]:
# Drop all text to lowercase
autism_fem.title = autism_fem.title.str.lower() 
autism_fem.selftext = autism_fem.selftext.str.lower()

# Remove web links and text in square brackets
autism_fem.title =  [re.sub(r'http\S+', ' ', str(x)) for x in autism_fem.title]
autism_fem.selftext =  [re.sub(r'http\S+', ' ', str(x)) for x in autism_fem.selftext]
autism_fem.title =  [re.sub('\[.*?\]', ' ', str(x)) for x in autism_fem.title]
autism_fem.selftext =  [re.sub('\[.*?\]', ' ', str(x)) for x in autism_fem.selftext]


# Drop all text to lowercase
autism_gen.title = autism_gen.title.str.lower() 
autism_gen.selftext = autism_gen.selftext.str.lower()

# Remove web links and text in square brackets
autism_gen.title =  [re.sub(r'http\S+', ' ', str(x)) for x in autism_gen.title]
autism_gen.selftext =  [re.sub(r'http\S+', ' ', str(x)) for x in autism_gen.selftext]
autism_gen.title =  [re.sub('\[.*?\]', ' ', str(x)) for x in autism_gen.title]
autism_gen.selftext =  [re.sub('\[.*?\]', ' ', str(x)) for x in autism_gen.selftext]

In [12]:
# Clean the text in title and selftext columns
autism_fem.title =  [re.sub(r'[%s]' % re.escape(string.punctuation),' ', str(x)) for x in autism_fem.title] # remove punctuation
autism_fem.title =  [re.sub('\w*\d\w*',' ', str(x)) for x in autism_fem.title] # remove words with a digit in them
autism_fem.title =  [re.sub('[‘’“”…—]',' ', str(x)) for x in autism_fem.title] # remove addt'l punctuation
autism_fem.title =  [re.sub('\n',' ', str(x)) for x in autism_fem.title] # remove newline chars
autism_fem.title =  [re.sub('\xa0',' ', str(x)) for x in autism_fem.title] # remove non-breaking space
autism_fem.title =  [e.demojize(x) for x in autism_fem.title] # remove emojis
autism_fem.title =  [re.sub(':[a-z_]*:',' ',x) for x in autism_fem.title] # remove emojis

autism_fem.selftext =  [re.sub(r'[%s]' % re.escape(string.punctuation),' ', str(x)) for x in autism_fem.selftext]
autism_fem.selftext =  [re.sub('\w*\d\w*',' ', str(x)) for x in autism_fem.selftext]
autism_fem.selftext =  [re.sub('[‘’“”…—]',' ', str(x)) for x in autism_fem.selftext]
autism_fem.selftext =  [re.sub('\n',' ', str(x)) for x in autism_fem.selftext]
autism_fem.selftext =  [re.sub('\xa0',' ', str(x)) for x in autism_fem.selftext]
autism_fem.selftext =  [e.demojize(x) for x in autism_fem.selftext] 
autism_fem.selftext =  [re.sub(':[a-z_]*:',' ',x) for x in autism_fem.selftext] 


# Clean the text in title and selftext columns
autism_gen.title =  [re.sub(r'[%s]' % re.escape(string.punctuation),' ', str(x)) for x in autism_gen.title] # remove punctuation
autism_gen.title =  [re.sub('\w*\d\w*',' ', str(x)) for x in autism_gen.title] # remove words with a digit in them
autism_gen.title =  [re.sub('[‘’“”…—]',' ', str(x)) for x in autism_gen.title] # remove addt'l punctuation
autism_gen.title =  [re.sub('\n',' ', str(x)) for x in autism_gen.title] # remove newline chars
autism_gen.title =  [re.sub('\xa0',' ', str(x)) for x in autism_gen.title] # remove non-breaking space
autism_gen.title =  [e.demojize(x) for x in autism_gen.title] # remove emojis
autism_gen.title =  [re.sub(':[a-z_]*:',' ',x) for x in autism_gen.title] # remove emojis

autism_gen.selftext =  [re.sub(r'[%s]' % re.escape(string.punctuation),' ', str(x)) for x in autism_gen.selftext]
autism_gen.selftext =  [re.sub('\w*\d\w*',' ', str(x)) for x in autism_gen.selftext]
autism_gen.selftext =  [re.sub('[‘’“”…—]',' ', str(x)) for x in autism_gen.selftext]
autism_gen.selftext =  [re.sub('\n',' ', str(x)) for x in autism_gen.selftext]
autism_gen.selftext =  [re.sub('\xa0',' ', str(x)) for x in autism_gen.selftext]
autism_gen.selftext =  [e.demojize(x) for x in autism_gen.selftext] 
autism_gen.selftext =  [re.sub(':[a-z_]*:',' ',x) for x in autism_gen.selftext] 

# NOTE: I still need to remove common words that contained apostrophes (i'm, they're, don't, etc.)
# which I'll do after tokenization

In [13]:
# Remove repeated spaces to clean everything up
autism_fem.title =  [re.sub(' +', ' ',x) for x in autism_fem.title] 
autism_fem.selftext =  [re.sub(' +', ' ',x) for x in autism_fem.selftext] 

# Remove repeated spaces to clean everything up
autism_gen.title =  [re.sub(' +', ' ',x) for x in autism_gen.title] 
autism_gen.selftext =  [re.sub(' +', ' ',x) for x in autism_gen.selftext] 


In [14]:
# Combine title text + paragraph text in a new column, 'full_text'
autism_fem['full_text'] = autism_fem.title + ' ' + autism_fem.selftext
autism_gen['full_text'] = autism_gen.title + ' ' + autism_gen.selftext

autism_fem.head(10)

ID                                              title  \
0  lggazi                            origin story megathread   
1  n0gss1                    diagnostic resources megathread   
2  ui4wn0        i wish there was ibuprofen for mental pain    
3  uhtqy1      i don t really do anything i just think a lot   
4  uhsjkb  found in motivational subreddit but thought ap...   
5  ui7j1b  is there an nt friendly way to request that pe...   
6  ui47s5  when not understanding how to communicate blow...   
7  ui3udh  what s something great for your mental health ...   
8  ui1sts  did i just inadvertently make my end of life p...   
9  uhyn6k                          well i guess he knows now   

                author         created_utc  score  upvote_ratio  \
0          idungonwent 2021-02-09 23:20:33    360          1.00   
1          LadyJohanna 2021-04-28 15:03:22    349          1.00   
2     AnnoyingSmartass 2022-05-04 11:58:58     61          0.98   
3        somethingtonn 2022-05-04 00:05:38    296          1.00   
4      Blue_Sunflower7 2022-05-03 23:03:33    231          0.99   
5  Throwwayeleventytwo 2022-05-04 14:13:03     12          0.88   
6        SpectrumFlyer 2022-05-04 11:17:18     19          0.92   
7           Penny_Luck 2022-05-04 10:53:23     18          0.96   
8       amillefolium11 2022-05-04 08:21:00     24          0.94   
9        SpectrumFlyer 2022-05-04 04:34:46     49          0.89   

                                            selftext       name  num_comments  \
0  we get a lot of foot traffic from people who a...  t3_lggazi           323   
1  hi amazing aspergirls since there are so many ...  t3_n0gss1           292   
2  i m so noise sensitive cars and sitting in the...  t3_ui4wn0            11   
3  maladaptive daydreaming creating scenarios to ...  t3_uhtqy1            60   
4                                                     t3_uhsjkb             0   
5  i have to be on this group text for my son s b...  t3_ui7j1b            44   
6   so i promise i am not trying to use this subr...  t3_ui47s5             3   
7  i went swimming yesterday i purposefully decid...  t3_ui3udh             7   
8                                                     t3_ui1sts             3   
9  just minutes after my last post and i have som...  t3_uhyn6k             9   

                                           full_text  
0  origin story megathread we get a lot of foot t...  
1  diagnostic resources megathread hi amazing asp...  
2  i wish there was ibuprofen for mental pain  i ...  
3  i don t really do anything i just think a lot ...  
4  found in motivational subreddit but thought ap...  
5  is there an nt friendly way to request that pe...  
6  when not understanding how to communicate blow...  
7  what s something great for your mental health ...  
8  did i just inadvertently make my end of life p...  
9  well i guess he knows now just minutes after m...

In [15]:
autism_gen.head(10)

ID                                              title  \
0  ub3skp  let s talk about aba therapy aba posts outside...   
1  ui3d78                                        i feel seen   
2  ui2rit                                   it s a spectrum    
3  uhziqv                                           my goals   
4  ui5crm  wanted to share an oil painting of a white hor...   
5  uhtyl3  i have ocd autism adhd and a math learning dis...   
6  ui4dv3                               i just can t keep up   
7  ui7uvw                               happy star wars day    
8  ui335q            her current special interests is snoopy   
9  uhpuuz  sometimes clear and concise communication is n...   

                 author         created_utc  score  upvote_ratio  \
0          cakeisatruth 2022-04-24 20:40:56    113          0.98   
1             Hassaan18 2022-05-04 10:20:14    872          0.98   
2     Duchamp_in_motion 2022-05-04 09:36:02    425          0.99   
3            stevekimes 2022-05-04 05:31:22    489          0.97   
4               Lova___ 2022-05-04 12:23:58    121          0.98   
5  ToraThePillowCuddler 2022-05-04 00:16:49    924          0.98   
6               vimiyui 2022-05-04 11:27:57     86          0.96   
7       cookienator1111 2022-05-04 14:28:43     52          0.98   
8        almondtree2018 2022-05-04 10:00:17     89          0.98   
9           topman20000 2022-05-03 20:59:57    700          0.99   

                                            selftext       name  num_comments  \
0  aba applied behavior analysis therapy is one o...  t3_ub3skp           230   
1                                                     t3_ui3d78            86   
2                                                     t3_ui2rit            52   
3                                                     t3_uhziqv            32   
4                                                     t3_ui5crm            17   
5                                                     t3_uhtyl3           131   
6                                                     t3_ui4dv3             8   
7                                                     t3_ui7uvw             5   
8                                                     t3_ui335q             6   
9                                                     t3_uhpuuz           156   

                                           full_text  
0  let s talk about aba therapy aba posts outside...  
1                                       i feel seen   
2                                  it s a spectrum    
3                                          my goals   
4  wanted to share an oil painting of a white hor...  
5  i have ocd autism adhd and a math learning dis...  
6                              i just can t keep up   
7                              happy star wars day    
8           her current special interests is snoopy   
9  sometimes clear and concise communication is n...

In [16]:
# Take a look at the cleaned corpus of text
corpus_clean = list(autism_fem.full_text)
corpus_clean

['origin story megathread we get a lot of foot traffic from people who are in the process of discovering investigating and considering an autism diagnosis this is a very turbulent time and people going through this discovery process want to know if they are on the right track unfortunately we are not medical professionals and we cannot give any advice on what individual people should or should not do however those of us who have gone through this process can still help by sharing our experience with it hopefully the new people will see a story in the comments that they resonate with so please tell us your origin story regale us with tales of how you discovered the world s most unusual superpower questions we see lot are how did you first learn about the way autism presents in girls when did you realize you fit on the spectrum what made you realize you were autistic is going after a diagnosis worth it what is the diagnosis process like ',
 'diagnostic resources megathread hi amazing asp

In [17]:
# Pickle for later
autism_fem.to_pickle('autism_fem.pkl')
autism_gen.to_pickle('autism_gen.pkl')


# NLP analysis

In [18]:
autism_fem = pd.read_pickle('autism_fem.pkl')
autism_gen = pd.read_pickle('autism_gen.pkl')

# Create corpus of all the text
corpus_f = list(autism_fem.full_text)
corpus_g = list(autism_gen.full_text)

In [19]:
corpus_f

['origin story megathread we get a lot of foot traffic from people who are in the process of discovering investigating and considering an autism diagnosis this is a very turbulent time and people going through this discovery process want to know if they are on the right track unfortunately we are not medical professionals and we cannot give any advice on what individual people should or should not do however those of us who have gone through this process can still help by sharing our experience with it hopefully the new people will see a story in the comments that they resonate with so please tell us your origin story regale us with tales of how you discovered the world s most unusual superpower questions we see lot are how did you first learn about the way autism presents in girls when did you realize you fit on the spectrum what made you realize you were autistic is going after a diagnosis worth it what is the diagnosis process like ',
 'diagnostic resources megathread hi amazing asp

In [20]:
corpus_g

['let s talk about aba therapy aba posts outside this thread will be removed  aba applied behavior analysis therapy is one of our most commonly discussed topics here and one of the most emotionally charged in an effort to declutter the sub and reduce rule breaking posts this will serve as the master thread for aba discussion this is the place for asking questions sharing personal experiences linking to blog posts or scientific articles and posting opinions if you re a parent seeking alternatives to aba please give us a little information about your child their age and what goals you have for them are usually enough please keep it civil abusive or harassing comments will be removed what is aba from aba therapy attempts to modify and encourage certain behaviors particularly in autistic children it is not a cure for asd but it can help individuals improve and develop an array of skills this form of therapy is rooted in behaviorist theories this assumes that reinforcement can increase or d

#### Document Term Matrix

In [21]:
add_stop_words = ['autism', 'autistic', 'asd', 'like', 'just', 'really', 'don','t', 'i','m', 've', 'they','re', 
                  'd', 'isn', 'll', 'what','s', 'that', 'he', 'she','a', 'didn', 'wasn']

# Add new stop words
stop_words = text.ENGLISH_STOP_WORDS.union(add_stop_words)


In [22]:
# Create document term matrix from corpus (includes title + paragraph text)
cv = CountVectorizer(stop_words=stop_words,min_df=0.01)
X = cv.fit_transform(corpus_f)
dtm_f = pd.DataFrame(X.toarray(), columns=cv.get_feature_names())

# Create dtm with totals in entire corpus
total_dtm_f = dtm_f.sum()  
total_dtm_f

ability        89
able          546
absolutely    174
abusive        64
accept        104
             ... 
years         747
yes           117
yesterday     122
young         107
younger       115
Length: 1077, dtype: int64

In [23]:
total_dtm_f.sort_values(ascending=False).head(20)

people     3508
feel       3209
know       2607
time       2109
things     1680
want       1583
think      1581
life       1256
way        1244
work       1175
make       1118
lot        1116
does        975
social      962
friends     931
need        923
say         910
said        898
day         896
going       894
dtype: int64

In [24]:
# Create document term matrix from corpus (includes title + paragraph text)
cv = CountVectorizer(stop_words=stop_words,min_df=0.01) 
X = cv.fit_transform(corpus_g)
dtm_g = pd.DataFrame(X.toarray(), columns=cv.get_feature_names())
total_dtm_g = dtm_g.sum()  
total_dtm_g.sort_values(ascending=False).head(20)

people     2812
feel       1763
know       1603
time       1283
things     1126
want       1027
think      1026
life        853
way         786
make        739
lot         723
does        691
say         682
social      654
work        643
friends     642
going       619
got         609
person      579
good        574
dtype: int64

#### Interestingly, the forums for female-specific autism vs general population autism have a very strong overlap in their top terms. I checked for cross-posting and duplicate posts across the two datasets.
#### It will be necessary and interesting to see at what point the datasets differ.

In [25]:
# Find top words - nouns only

def collect_nouns(text):
    pos_list = pos_tag(word_tokenize(text))
    nouns = ''
    for item in pos_list:
        if item[1] == 'NN':
            nouns = nouns + item[0] + ' '
    return nouns 

autism_fem['full_text_nouns'] = autism_fem.full_text.map(collect_nouns)
autism_fem

ID                                              title  \
0     lggazi                            origin story megathread   
1     n0gss1                    diagnostic resources megathread   
2     ui4wn0        i wish there was ibuprofen for mental pain    
3     uhtqy1      i don t really do anything i just think a lot   
4     uhsjkb  found in motivational subreddit but thought ap...   
...      ...                                                ...   
3811  t1cqdy          i am not handling the ukraine crisis well   
3812  spzfpi  has anyone seen the study that autistics and s...   
3813  qi6g2b  i literally just fixed my biggest quality of l...   
3814  qe55ry         i want friends but i can t relate to moms    
3815  niy0c2  anyone else feeling anxious about returning to...   

                  author         created_utc  score  upvote_ratio  \
0            idungonwent 2021-02-09 23:20:33    360          1.00   
1            LadyJohanna 2021-04-28 15:03:22    349          1.00   
2       AnnoyingSmartass 2022-05-04 11:58:58     61          0.98   
3          somethingtonn 2022-05-04 00:05:38    296          1.00   
4        Blue_Sunflower7 2022-05-03 23:03:33    231          0.99   
...                  ...                 ...    ...           ...   
3811  constantcomprimise 2022-02-25 19:49:33    150          0.98   
3812              080341 2022-02-11 13:28:08    150          0.99   
3813     danceswithronin 2021-10-29 06:27:08    151          0.98   
3814        _littlearies 2021-10-23 13:40:25    154          0.98   
3815  solipsisticcompass 2021-05-23 02:26:09    152          0.99   

                                               selftext       name  \
0     we get a lot of foot traffic from people who a...  t3_lggazi   
1     hi amazing aspergirls since there are so many ...  t3_n0gss1   
2     i m so noise sensitive cars and sitting in the...  t3_ui4wn0   
3     maladaptive daydreaming creating scenarios to ...  t3_uhtqy1   
4                                                        t3_uhsjkb   
...                                                 ...        ...   
3811  that s it really i am not handling this well a...  t3_t1cqdy   
3812  from wikipedia bufotenin ho dmt bufotenine is ...  t3_spzfpi   
3813  i ve been dealing with an indentation in my ma...  t3_qi6g2b   
3814  i m and it seems like everyone around me is ei...  t3_qe55ry   
3815  my masks have become a source of comfort and s...  t3_niy0c2   

      num_comments                                          full_text  \
0              323  origin story megathread we get a lot of foot t...   
1              292  diagnostic resources megathread hi amazing asp...   
2               11  i wish there was ibuprofen for mental pain  i ...   
3               60  i don t really do anything i just think a lot ...   
4                0  found in motivational subreddit but thought ap...   
...            ...                                                ...   
3811            61  i am not handling the ukraine crisis well that...   
3812           139  has anyone seen the study that autistics and s...   
3813             7  i literally just fixed my biggest quality of l...   
3814            65  i want friends but i can t relate to moms  i m...   
3815            52  anyone else feeling anxious about returning to...   

                                        full_text_nouns  
0     story megathread lot foot traffic process inve...  
1     aspergirls area megathread information process...  
2     ibuprofen pain tram mental pain nothing i part...  
3     anything lot head lifetime i ve time house i l...  
4                                subreddit appropriate   
...                                                 ...  
3811  i crisis well i news i work i anyone boat news...  
3812  anyone study bufotenin urine bufotenin ho dmt ...  
3813  quality life issue indentation mattress mattre...  
3814  i m everyone male mom i interest lot guess i g...  
3815  anyone source 

In [26]:
autism_gen['full_text_nouns'] = autism_gen.full_text.map(collect_nouns)
autism_gen

ID                                              title  \
0     ub3skp  let s talk about aba therapy aba posts outside...   
1     ui3d78                                        i feel seen   
2     ui2rit                                   it s a spectrum    
3     uhziqv                                           my goals   
4     ui5crm  wanted to share an oil painting of a white hor...   
...      ...                                                ...   
3972  p5y3py  why do nt people get upset when you respond wi...   
3973  omqmix  do you ever feel overwhelmed when learning new...   
3974  i8q5np                           i m worried for you guys   
3975  heedhr  wrinkles in bedsheets under my body drive me nuts   
3976  gmfhqg  i realized today that part of the reason i com...   

                 author         created_utc  score  upvote_ratio  \
0          cakeisatruth 2022-04-24 20:40:56    113          0.98   
1             Hassaan18 2022-05-04 10:20:14    872          0.98   
2     Duchamp_in_motion 2022-05-04 09:36:02    425          0.99   
3            stevekimes 2022-05-04 05:31:22    489          0.97   
4               Lova___ 2022-05-04 12:23:58    121          0.98   
...                 ...                 ...    ...           ...   
3972          Lavapulse 2021-08-17 06:13:12    425          0.98   
3973        SmokinJoe93 2021-07-18 13:35:01    426          1.00   
3974          lumpyeuph 2020-08-13 00:51:51    429          0.97   
3975          zopiclown 2020-06-23 13:13:12    428          0.98   
3976               None 2020-05-19 02:04:46    429          0.99   

                                               selftext       name  \
0     aba applied behavior analysis therapy is one o...  t3_ub3skp   
1                                                        t3_ui3d78   
2                                                        t3_ui2rit   
3                                                        t3_uhziqv   
4                                                        t3_ui5crm   
...                                                 ...        ...   
3972  for example if i m asked can you do x the aske...  t3_p5y3py   
3973  over the last year since the market crash of p...  t3_omqmix   
3974  i ve seen a lot of stories on here lately that...  t3_i8q5np   
3975  whether it s a wrinkle in a bedsheet under my ...  t3_heedhr   
3976  i m just not interested in talking to most peo...  t3_gmfhqg   

      num_comments                                          full_text  \
0              230  let s talk about aba therapy aba posts outside...   
1               86                                       i feel seen    
2               52                                  it s a spectrum     
3               32                                          my goals    
4               17  wanted to share an oil painting of a white hor...   
...            ...                                                ...   
3972           100  why do nt people get upset when you respond wi...   
3973            39  do you ever feel overwhelmed when learning new...   
3974           116  i m worried for you guys i ve seen a lot of st...   
3975            65  wrinkles in bedsheets under my body drive me n...   
3976            49  i realized today that part of the reason i com...   

                                        full_text_nouns  
0     therapy aba thread analysis therapy effort sub...  
1                                                    i   
2                                             spectrum   
3                                                        
4                           share oil painting horse i   
...                                                 ...  
3972  anything certainty example asker answer anythi...  
3973  time year market crash part routine i research...  
3974  lot problem i front i one suit shit someone th...  
3975  body wrinkle bedsheet body dirt skin shirt ski...  
3976  i today part reason jerk i

In [27]:
corpus_noun_f = list(autism_fem.full_text_nouns)

# Recreate document-term matrix

cv = CountVectorizer(stop_words=stop_words,min_df=0.01) #,min_df=0.01,ngram_range=(2, 3)
X = cv.fit_transform(corpus_noun_f)
dtm_n_f = pd.DataFrame(X.toarray(), columns=cv.get_feature_names())

# Create dtm with totals in entire corpus
dtm_total_n_f = dtm_n_f.sum()  

# Top words used in entire corpus
dtm_total_n_f.sort_values(ascending=False).head(20)

time          2109
life          1256
way           1244
lot           1115
day            896
person         887
thing          837
work           817
diagnosis      742
job            645
school         518
anxiety        487
friend         481
family         480
today          476
kind           465
experience     425
help           422
point          416
advice         413
dtype: int64

In [28]:
corpus_noun_g = list(autism_gen.full_text_nouns)

# Recreate document-term matrix

cv = CountVectorizer(stop_words=stop_words,min_df=0.01) #,min_df=0.01,ngram_range=(2, 3)
X = cv.fit_transform(corpus_noun_g)
dtm_n_g = pd.DataFrame(X.toarray(), columns=cv.get_feature_names())

# Create dtm with totals in entire corpus
dtm_total_n_g = dtm_n_g.sum()  

# Top words used in entire corpus
dtm_total_n_g.sort_values(ascending=False).head(20)

time         1283
life          853
way           786
lot           722
person        579
day           565
thing         546
school        485
job           446
work          434
diagnosis     332
year          318
family        312
point         301
spectrum      297
friend        279
today         276
world         270
kind          269
anxiety       262
dtype: int64

#### Again, there is a very strong overlap in top nouns in the forums for female-specific autism vs general population
#### I find this odd, but can't find errors in how these are generated

In [29]:
# These are the top nouns in the female forum that are not in the general forum (top 200)
counter = 0
overlap_list = []
not_in_common = []
for term in dtm_total_n_f.sort_values(ascending=False).head(200).index:
    if term in dtm_total_n_g.sort_values(ascending=False).head(200).index:
        counter+=1
        overlap_list.append(term)
    else:
        not_in_common.append(term)
counter,not_in_common

(170,
 ['husband',
  'hair',
  'burnout',
  'boyfriend',
  'mask',
  'assessment',
  'interview',
  'trauma',
  'appointment',
  'masking',
  'period',
  'skin',
  'boss',
  'gender',
  'teacher',
  'meeting',
  'effort',
  'water',
  'daughter',
  'plan',
  'tone',
  'office',
  'fear',
  'store',
  'friendship',
  'routine',
  'overload',
  'thinking',
  'stim',
  'think'])

In [30]:
# These are the top *words* in the female forum that are not in the general forum (top 200)
counter = 0
overlap_list = []
not_in_common = []
for term in total_dtm_f.sort_values(ascending=False).head(200).index:
    if term in total_dtm_g.sort_values(ascending=False).head(200).index:
        counter+=1
        overlap_list.append(term)
    else:
        not_in_common.append(term)
counter,not_in_common

(178,
 ['women',
  'masking',
  'mask',
  'experiences',
  'therapist',
  'super',
  'partner',
  'body',
  'wondering',
  'upset',
  'nice',
  'food',
  'feelings',
  'difficult',
  'lol',
  'taking',
  'overwhelmed',
  'took',
  'health',
  'realized',
  'woman',
  'face'])

#### I could also try finding the difference in counts for each word (find the largest differences) in the two forums. TODO

# Sentiment Analysis with VADER

In [31]:
analyzer = SentimentIntensityAnalyzer()
autism_fem['sentiment_score'] = autism_fem.full_text.map(analyzer.polarity_scores).map(lambda x: x.get('compound'))
autism_fem.head()

ID                                              title  \
0  lggazi                            origin story megathread   
1  n0gss1                    diagnostic resources megathread   
2  ui4wn0        i wish there was ibuprofen for mental pain    
3  uhtqy1      i don t really do anything i just think a lot   
4  uhsjkb  found in motivational subreddit but thought ap...   

             author         created_utc  score  upvote_ratio  \
0       idungonwent 2021-02-09 23:20:33    360          1.00   
1       LadyJohanna 2021-04-28 15:03:22    349          1.00   
2  AnnoyingSmartass 2022-05-04 11:58:58     61          0.98   
3     somethingtonn 2022-05-04 00:05:38    296          1.00   
4   Blue_Sunflower7 2022-05-03 23:03:33    231          0.99   

                                            selftext       name  num_comments  \
0  we get a lot of foot traffic from people who a...  t3_lggazi           323   
1  hi amazing aspergirls since there are so many ...  t3_n0gss1           292   
2  i m so noise sensitive cars and sitting in the...  t3_ui4wn0            11   
3  maladaptive daydreaming creating scenarios to ...  t3_uhtqy1            60   
4                                                     t3_uhsjkb             0   

                                           full_text  \
0  origin story megathread we get a lot of foot t...   
1  diagnostic resources megathread hi amazing asp...   
2  i wish there was ibuprofen for mental pain  i ...   
3  i don t really do anything i just think a lot ...   
4  found in motivational subreddit but thought ap...   

                                     full_text_nouns  sentiment_score  
0  story megathread lot foot traffic process inve...           0.9324  
1  aspergirls area megathread information process...           0.9348  
2  ibuprofen pain tram mental pain nothing i part...          -0.9583  
3  anything lot head lifetime i ve time house i l...           0.8402  
4                             subreddit appropriate            0.0000

In [32]:
# highest score
highest_sentiment = autism_fem.iloc[autism_fem.sentiment_score.idxmax()]
highest_sentiment.selftext

' happy weekend everybody let s spend some time to refocus ourselves on the self care we probably neglected this week because of commitments like school work family and so on take some time out for yourself today and tomorrow remember that you matter and be extra kind and mindful in taking care of your own mind and body and living environment take some time to tidy up your habitat surround yourself with a happy living space that s set up exactly how you like it so you can relax instead of feeling guilty about not having the spoons to take care of it all week timers are your friend your very very best friend if a task seems super daunting then set a short timer and start doing the thing when the time s up you ve accomplished a goal we ve added suggestions below to help get you going modify those to your own liking you ll be amazed what you can get done in minutes because you re awesome like that please share your own tips and tricks and success stories with the rest of the community we 

In [33]:
# lowest score
autism_fem.iloc[autism_fem.sentiment_score.idxmin()]
lowest_sentiment = autism_fem.iloc[autism_fem.sentiment_score.idxmin()]#['sentiment_score']
lowest_sentiment.selftext

' i have been involuntarily held at a juvenile psychiatric ward twice in my life it was the same place both times the first time for a week and the second for a month this post is a response to so you re going to be hospitalized involuntarily please don t torment the writer of that one i m autistic of course so i can give my feedback on both my experience and her post trigger warning basically any graphic topic you can think of including ptsd forced medication starvation suicide and bullying please excuse me past op of the post i m responding to if i ve misinterpreted your words at all addressing what they said you re not going to like it they are completely right let me be clear that their post to me and many others reads as very distant unempathetic condescending apathetic and not focused on healing at all whatsoever for whoever must go into these places they re probably not reflecting their feelings on the matter they re reflecting the system by which these facilities run they re mi

#### Not sure how to implement sentiment analysis into something useful. I could compare overall sentiment of the two datasets.

In [34]:
autism_fem.sentiment_score.mean()

0.22530948637316536

In [35]:
analyzer = SentimentIntensityAnalyzer()
autism_gen['sentiment_score'] = autism_gen.full_text.map(analyzer.polarity_scores).map(lambda x: x.get('compound'))
autism_gen.sentiment_score.mean()

0.17130829771184308

# Topic Modeling

### Latent Semantic Analysis

In [36]:
# Create document term matrix again from corpus
vectorizer = CountVectorizer(stop_words=stop_words,min_df=0.001)
doc_term = vectorizer.fit_transform(corpus_noun_f)
doc_term.shape

(3816, 2232)

In [37]:
# Make dtm into a df
doc_term_df = pd.DataFrame(doc_term.toarray(), index=corpus_noun_f, columns=vectorizer.get_feature_names())
doc_term_df

aba  abandonment  ability  \
story megathread lot foot traffic process inves...    0            0        0   
aspergirls area megathread information process ...    0            0        0   
ibuprofen pain tram mental pain nothing i part ...    0            0        0   
anything lot head lifetime i ve time house i li...    0            0        0   
subreddit appropriate                                 0            0        0   
...                                                 ...          ...      ...   
i crisis well i news i work i anyone boat news ...    0            0        0   
anyone study bufotenin urine bufotenin ho dmt b...    0            0        0   
quality life issue indentation mattress mattres...    0            0        0   
i m everyone male mom i interest lot guess i gr...    0            0        0   
anyone source comfort security year time overlo...    0            0        0   

                                                    ableism  ableist  absence  \
story megathread lot foot traffic process inves...        0        0        0   
aspergirls area megathread information process ...        0        0        0   
ibuprofen pain tram mental pain nothing i part ...        0        0        0   
anything lot head lifetime i ve time house i li...        0        0        0   
subreddit appropriate                                     0        0        0   
...                                                     ...      ...      ...   
i crisis well i news i work i anyone boat news ...        0        0        0   
anyone study bufotenin urine bufotenin ho dmt b...        0        0        0   
quality life issue indentation mattress mattres...        0        0        0   
i m everyone male mom i interest lot guess i gr...        0        0        0   
anyone source comfort security year time overlo...        0        0        0   

                                                    absolute  abuse  abuser  \
story megathread lot foot traffic process inves...         0      0       0   
aspergirls area megathread information process ...         0      0       0   
ibuprofen pain tram mental pain nothing i part ...         0      0       0   
anything lot head lifetime i ve time house i li...         0      0       0   
subreddit appropriate                                      0      0       0   
...                                                      ...    ...     ...   
i crisis well i news i work i anyone boat news ...         0      0       0   
anyone study bufotenin urine bufotenin ho dmt b...         0      0       0   
quality life issue indentation mattress mattres...         0      0       0   
i m everyone male mom i interest lot guess i gr...         0      0       0   
anyone source comfort security year time overlo...         0      0       0   

                                                    accent  ...  yesterday  \
story megathread lot foot traffic process inves...       0  ...          0   
aspergirls area megathread information process ...       0  ...          0   
ibuprofen pain tram mental pain nothing i part ...       0  ...          0   
anything lot head lifetime i ve time house i li...       0  ...          0   
subreddit appropriate                                    0  ...          0   
...                                                    ...  ...        ...   
i crisis well i news i work i anyone boat news ...       0  ...          0   
anyone study bufotenin urine bufotenin ho dmt b...       0  ...          0   
quality life issue indentation mattress mattres...       0  ...          0   
i m everyone male mom i interest lot guess i gr...       0  ...          0   
anyone source comfort security year time overlo...       0  ...          0   

                                                    yo  youre  youth  youtube  \
story megathread lot foot traffic process inves...   0      0      0        0   
aspergirls area megathread information process ...   0    

In [38]:
# Fit an LSA model using TruncatedSVD
lsa = TruncatedSVD(15)
lsa.fit(doc_term)
lsa

TruncatedSVD(n_components=15)

In [39]:
topic_term = lsa.components_.round(3)
topic_term

array([[ 0.002,  0.001,  0.016, ...,  0.   ,  0.008,  0.014],
       [-0.001,  0.003,  0.003, ..., -0.   , -0.017, -0.031],
       [ 0.001,  0.   ,  0.007, ...,  0.   , -0.015, -0.037],
       ...,
       [ 0.004,  0.001, -0.013, ...,  0.   ,  0.006,  0.02 ],
       [ 0.001,  0.002,  0.007, ...,  0.   ,  0.015,  0.053],
       [-0.006,  0.002, -0.007, ...,  0.   ,  0.005,  0.026]])

In [40]:
topic_term_df = pd.DataFrame(topic_term.round(3),
                index = ["component_1", "component_2", "component_3", "component_4", "component_5",
                        "component_6", "component_7", "component_8", "component_9", "component_10",
                        "component_11", "component_12", "component_13", "component_14", "component_15"], 
                columns = vectorizer.get_feature_names())
topic_term_df

aba  abandonment  ability  ableism  ableist  absence  \
component_1   0.002        0.001    0.016    0.004    0.001    0.001   
component_2  -0.001        0.003    0.003    0.007   -0.000    0.000   
component_3   0.001        0.000    0.007   -0.000   -0.001    0.004   
component_4   0.001       -0.003   -0.002    0.010    0.000    0.000   
component_5   0.004       -0.001   -0.006    0.001    0.000   -0.002   
component_6  -0.005        0.002    0.010    0.004    0.001    0.003   
component_7  -0.003       -0.001    0.002   -0.001    0.001   -0.002   
component_8  -0.004       -0.001   -0.006    0.005   -0.000    0.000   
component_9   0.004       -0.001    0.010   -0.001   -0.000    0.001   
component_10 -0.002       -0.002   -0.003   -0.002   -0.001    0.000   
component_11  0.001       -0.001    0.013   -0.008   -0.001   -0.007   
component_12  0.002       -0.002    0.009    0.005    0.001    0.001   
component_13  0.004        0.001   -0.013    0.008   -0.000    0.001   
component_14  0.001        0.002    0.007   -0.003    0.001   -0.001   
component_15 -0.006        0.002   -0.007   -0.009    0.001    0.002   

              absolute  abuse  abuser  accent  ...  yesterday     yo  youre  \
component_1      0.002  0.009   0.001   0.002  ...      0.019  0.003  0.001   
component_2     -0.002  0.014   0.001   0.001  ...     -0.004 -0.004  0.000   
component_3      0.002 -0.001   0.000   0.000  ...      0.014 -0.002 -0.000   
component_4      0.003 -0.004  -0.001   0.004  ...      0.005  0.003  0.002   
component_5      0.001  0.005  -0.001  -0.001  ...      0.009  0.001  0.000   
component_6     -0.001  0.003  -0.003   0.001  ...     -0.004 -0.008 -0.001   
component_7      0.001  0.004  -0.000  -0.002  ...      0.012 -0.000  0.001   
component_8      0.002 -0.001  -0.002   0.001  ...      0.010 -0.002  0.003   
component_9     -0.001  0.003  -0.001   0.000  ...     -0.012 -0.001  0.001   
component_10    -0.002  0.020   0.000  -0.000  ...     -0.009  0.004  0.001   
component_11     0.002  0.011   0.001   0.006  ...      0.008 -0.002 -0.000   
component_12    -0.001  0.005  -0.002   0.001  ...     -0.012  0.002 -0.002   
component_13    -0.002  0.020   0.002  -0.001  ...      0.004  0.003  0.000   
component_14    -0.002  0.010   0.001  -0.005  ...     -0.002 -0.006 -0.000   
component_15    -0.000  0.011   0.001  -0.001  ...      0.016  0.001  0.003   

              youth  youtube     yr   zero  zombie   zone   zoom  
component_1   0.002    0.006  0.001  0.001   0.000  0.008  0.014  
component_2   0.001    0.000 -0.001  0.000  -0.000 -0.017 -0.031  
component_3  -0.001   -0.001 -0.001  0.000   0.000 -0.015 -0.037  
component_4  -0.003   -0.004 -0.000  0.002   0.000 -0.006 -0.023  
component_5  -0.004    0.000  0.000 -0.000   0.000  0.004 -0.000  
component_6  -0.000   -0.003 -0.000  0.001  -0.001  0.004  0.023  
component_7   0.001   -0.002 -0.000 -0.001   0.001 -0.007  0.010  
component_8   0.000   -0.004  0.001 -0.001  -0.000  0.001 -0.000  
component_9   0.004    0.006  0.001 -0.000  -0.000 -0.007 -0.010  
component_10 -0.001    0.000  0.002 -0.001  -0.000 -0.012 -0.038  
component_11  0.000    0.000  0.001 -0.000   0.000 -0.005 -0.022  
component_12 -0.001    0.007 -0.002  0.002   0.002  0.024  0.088  
component_13 -0.002   -0.007  0.001 -0.001   0.000  0.006  0.020  
component_14  0.003   -0.006 -0.000 -0.001   0.000  0.015  0.053  
component_15  0.002    0.003  0.001  0.002   0.000  0.005  0.026  

[15 rows x 2232 columns]

In [41]:
# Function to display the top n terms in each topic
def display_topics(model, feature_names, no_top_words, topic_names = None): 
    for ix, topic in enumerate(model.components_):
        if not topic_names or not topic_names[ix]:
            print("\nTopic ", ix + 1)
        else:
            print("\nTopic: ", topic_names[ix])
        print(", ".join([feature_names[i]
                        for i in topic.argsort()[:-no_top_words - 1:-1]]))
    print("\n")
    return model, feature_names, no_top_words

In [42]:
output = display_topics(lsa, vectorizer.get_feature_names(), 10)



Topic  1
time, life, way, lot, person, day, work, thing, diagnosis, job

Topic  2
life, diagnosis, way, lot, person, spectrum, anxiety, adhd, therapist, sense

Topic  3
job, work, day, lot, manager, today, boss, interview, home, coworker

Topic  4
person, way, lot, thing, friend, kind, relationship, problem, conversation, anxiety

Topic  5
diagnosis, lot, anxiety, spectrum, therapist, doctor, adhd, time, school, mom

Topic  6
person, job, diagnosis, time, work, group, spectrum, share, conversation, interview

Topic  7
day, diagnosis, way, room, person, staff, work, advice, post, today

Topic  8
way, time, life, anxiety, body, feel, job, hair, gender, sense

Topic  9
school, way, mom, job, college, year, friend, kid, girl, time

Topic  10
anxiety, family, advice, job, staff, help, room, place, relationship, home

Topic  11
work, thing, family, home, advice, place, room, food, staff, cat

Topic  12
share, group, meeting, thing, advice, school, staff, experience, place, lot

Topic  13
lo

#### There is A LOT of overlap in words of the different topics

### Non-Negative Matrix Factorization (NMF)

In [43]:
# Create document term matrix again from corpus
vectorizer = CountVectorizer(stop_words=stop_words,min_df=0.01 ) # min_df=0.001 
doc_term = vectorizer.fit_transform(corpus_noun_f)
doc_term.shape

(3816, 310)

In [44]:
# Make dtm into a df
doc_term_df = pd.DataFrame(doc_term.toarray(), index=corpus_noun_f, columns=vectorizer.get_feature_names())
doc_term_df

ability  adhd  adult  \
story megathread lot foot traffic process inves...        0     0      0   
aspergirls area megathread information process ...        0     0      0   
ibuprofen pain tram mental pain nothing i part ...        0     0      0   
anything lot head lifetime i ve time house i li...        0     0      0   
subreddit appropriate                                     0     0      0   
...                                                     ...   ...    ...   
i crisis well i news i work i anyone boat news ...        0     0      0   
anyone study bufotenin urine bufotenin ho dmt b...        0     0      0   
quality life issue indentation mattress mattres...        0     0      0   
i m everyone male mom i interest lot guess i gr...        0     0      0   
anyone source comfort security year time overlo...        0     0      0   

                                                    advance  advice  age  \
story megathread lot foot traffic process inves...        0       1    0   
aspergirls area megathread information process ...        0       0    0   
ibuprofen pain tram mental pain nothing i part ...        0       0    0   
anything lot head lifetime i ve time house i li...        0       0    0   
subreddit appropriate                                     0       0    0   
...                                                     ...     ...  ...   
i crisis well i news i work i anyone boat news ...        0       0    0   
anyone study bufotenin urine bufotenin ho dmt b...        0       0    0   
quality life issue indentation mattress mattres...        0       0    0   
i m everyone male mom i interest lot guess i gr...        0       2    0   
anyone source comfort security year time overlo...        0       0    0   

                                                    anger  answer  anxiety  \
story megathread lot foot traffic process inves...      0       0        0   
aspergirls area megathread information process ...      0       0        0   
ibuprofen pain tram mental pain nothing i part ...      0       0        0   
anything lot head lifetime i ve time house i li...      0       0        0   
subreddit appropriate                                   0       0        0   
...                                                   ...     ...      ...   
i crisis well i news i work i anyone boat news ...      0       0        0   
anyone study bufotenin urine bufotenin ho dmt b...      0       0        0   
quality life issue indentation mattress mattres...      0       0        0   
i m everyone male mom i interest lot guess i gr...      0       0        0   
anyone source comfort security year time overlo...      0       0        0   

                                                    anybody  ...  way  week  \
story megathread lot foot traffic process inves...        0  ...    1     0   
aspergirls area megathread information process ...        0  ...    0     0   
ibuprofen pain tram mental pain nothing i part ...        0  ...    0     0   
anything lot head lifetime i ve time house i li...        0  ...    0     0   
subreddit appropriate                                     0  ...    0     0   
...                                                     ...  ...  ...   ...   
i crisis well i news i work i anyone boat news ...        0  ...    0     0   
anyone study bufotenin urine bufotenin ho dmt b...        0  ...    0     0   
quality life issue indentation mattress mattres...        0  ...    0     0   
i m everyone male mom i interest lot guess i gr...        0  ...    0     0   
anyone source comfort security year time overlo...        0  ...    0     0   

                                                    weekend  weird  woman  \
story megathread lot foot traffic process inves...        0      0      0   
aspergirls area megathread information process ...        0      0      0   
ibuprofen pain tram mental pain nothing i part ...        0      0      0   
anything lot head lifetime i ve 

In [45]:
nmf = NMF(15, init = "nndsvda")
nmf.fit(doc_term_df)

NMF(init='nndsvda', n_components=15)

In [46]:
topic_term = nmf.components_.round(3)
topic_term.shape

(15, 310)

In [47]:
topic_term_df = pd.DataFrame(topic_term.round(3),
                index = ["component_1", "component_2", "component_3", "component_4", "component_5",
                        "component_6", "component_7", "component_8", "component_9", "component_10",
                        "component_11", "component_12", "component_13", "component_14", "component_15"],
                columns = vectorizer.get_feature_names())
topic_term_df

ability   adhd  adult  advance  advice    age  anger  answer  \
component_1     0.032  0.000  0.000    0.027   0.000  0.000  0.000   0.082   
component_2     0.053  0.277  0.049    0.000   0.000  0.000  0.000   0.045   
component_3     0.031  0.000  0.009    0.075   0.160  0.000  0.000   0.024   
component_4     0.056  0.235  0.265    0.000   0.000  0.123  0.086   0.048   
component_5     0.005  0.957  0.362    0.047   0.000  0.222  0.000   0.094   
component_6     0.061  0.000  0.000    0.009   0.326  0.002  0.003   0.030   
component_7     0.000  0.039  0.000    0.015   0.000  0.064  0.061   0.006   
component_8     0.012  0.042  0.130    0.000   0.004  0.095  0.109   0.078   
component_9     0.059  0.152  0.203    0.031   0.000  0.239  0.000   0.000   
component_10    0.131  0.000  0.012    0.009   0.175  0.000  0.000   0.000   
component_11    0.083  0.302  0.000    0.036   0.860  0.000  0.000   0.000   
component_12    0.000  0.000  0.000    0.011   0.324  0.000  0.000   0.012   
component_13    0.000  0.000  0.000    0.021   0.000  0.000  0.037   0.078   
component_14    0.040  0.000  0.349    0.067   1.566  0.235  0.005   0.040   
component_15    0.086  0.000  0.036    0.013   0.581  0.000  0.006   0.038   

              anxiety  anybody  ...    way   week  weekend  weird  woman  \
component_1     0.000    0.000  ...  0.000  0.299    0.015  0.042  0.000   
component_2     0.000    0.047  ...  0.000  0.000    0.014  0.053  0.182   
component_3     0.000    0.000  ...  0.000  0.285    0.008  0.005  0.000   
component_4     0.000    0.000  ...  0.000  0.000    0.000  0.031  0.108   
component_5     0.000    0.000  ...  0.000  0.000    0.000  0.027  0.040   
component_6     0.000    0.039  ...  0.000  0.000    0.000  0.013  0.044   
component_7     0.000    0.015  ...  0.000  0.000    0.000  0.028  0.019   
component_8     0.000    0.068  ...  5.911  0.000    0.000  0.096  0.299   
component_9     0.000    0.006  ...  0.000  0.000    0.000  0.027  0.108   
component_10    0.000    0.033  ...  0.000  0.401    0.051  0.000  0.000   
component_11    8.274    0.000  ...  0.000  0.000    0.055  0.000  0.000   
component_12    0.000    0.067  ...  0.000  0.482    0.146  0.000  0.000   
component_13    0.000    0.000  ...  0.020  0.000    0.057  0.000  0.000   
component_14    0.000    0.000  ...  0.000  0.338    0.175  0.000  0.000   
component_15    0.000    0.002  ...  0.000  1.204    0.029  0.000  0.674   

               word   work  world   year  yesterday  
component_1   0.000  0.000  0.051  0.000      0.050  
component_2   0.131  0.000  0.182  0.028      0.033  
component_3   0.000  0.000  0.024  0.301      0.024  
component_4   0.000  0.000  0.860  0.223      0.000  
component_5   0.133  0.000  0.000  0.429      0.045  
component_6   0.104  0.000  0.277  0.000      0.000  
component_7   0.039  0.000  0.000  0.007      0.015  
component_8   0.098  0.000  0.296  0.000      0.069  
component_9   0.000  0.000  0.259  0.932      0.000  
component_10  0.015  7.129  0.094  0.136      0.132  
component_11  0.000  0.000  0.000  0.058      0.009  
component_12  0.057  0.000  0.000  0.026      0.168  
component_13  0.000  0.000  0.182  0.371      0.047  
component_14  0.008  0.000  0.210  0.804      0.089  
component_15  0.030  0.000  0.000  0.054      0.073  

[15 rows x 310 columns]

In [48]:
# Function to display the top n terms in each topic
def display_topics(model, feature_names, no_top_words, topic_names = None): 
    for ix, topic in enumerate(model.components_):
        if not topic_names or not topic_names[ix]:
            print("\nTopic ", ix + 1)
        else:
            print("\nTopic: ", topic_names[ix])
        print(", ".join([feature_names[i]
                        for i in topic.argsort()[:-no_top_words - 1:-1]]))
    print("\n")
    return model, feature_names, no_top_words

In [49]:
output = display_topics(nmf, vectorizer.get_feature_names(), 8)



Topic  1
time, husband, home, care, self, partner, appointment, energy

Topic  2
thing, brain, head, kind, sense, idea, bit, body

Topic  3
job, interview, manager, boss, position, help, month, company

Topic  4
life, world, care, health, therapy, self, therapist, adult

Topic  5
diagnosis, spectrum, therapist, adhd, doctor, self, health, support

Topic  6
person, relationship, conversation, kind, situation, point, advice, idea

Topic  7
lot, stuff, research, experience, mind, bit, cat, problem

Topic  8
way, sense, post, feel, reason, point, kind, place

Topic  9
school, year, college, mom, class, kid, teacher, girl

Topic  10
work, today, manager, office, home, week, problem, boss

Topic  11
anxiety, depression, relationship, disorder, advice, therapist, therapy, communication

Topic  12
day, night, today, home, house, room, bed, party

Topic  13
friend, party, friendship, night, group, house, year, problem

Topic  14
family, mom, home, advice, help, child, place, room

Topic  15
sh

#### NMF seems to separate the topics a little better than LSA

### Latent Dirichlet Allocation

In [50]:
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [51]:
term_doc = doc_term.transpose()
corpus = matutils.Sparse2Corpus(term_doc)
id2word = dict((v, k) for k, v in vectorizer.vocabulary_.items())
lda = models.LdaModel(corpus=corpus, num_topics=10, id2word=id2word, passes=10)
lda

2022-05-07 11:26:05,305 : INFO : using symmetric alpha at 0.1
2022-05-07 11:26:05,307 : INFO : using symmetric eta at 0.1
2022-05-07 11:26:05,307 : INFO : using serial LDA version on this node
2022-05-07 11:26:05,309 : INFO : running online (multi-pass) LDA training, 10 topics, 10 passes over the supplied corpus of 3816 documents, updating model once every 2000 documents, evaluating perplexity every 3816 documents, iterating 50x with a convergence threshold of 0.001000
2022-05-07 11:26:05,319 : INFO : PROGRESS: pass 0, at document #2000/3816
2022-05-07 11:26:05,966 : INFO : merging changes from 2000 documents into a model of 3816 documents
2022-05-07 11:26:05,967 : INFO : topic #9 (0.100): 0.035*"time" + 0.025*"share" + 0.025*"way" + 0.023*"lot" + 0.021*"day" + 0.019*"school" + 0.019*"thing" + 0.017*"life" + 0.016*"food" + 0.015*"person"
2022-05-07 11:26:05,967 : INFO : topic #4 (0.100): 0.046*"time" + 0.030*"life" + 0.025*"thing" + 0.025*"lot" + 0.025*"friend" + 0.022*"day" + 0.022*"w

2022-05-07 11:26:10,461 : INFO : topic #9 (0.100): 0.051*"school" + 0.032*"food" + 0.030*"music" + 0.025*"time" + 0.025*"way" + 0.021*"lot" + 0.019*"thing" + 0.016*"class" + 0.014*"stim" + 0.014*"place"
2022-05-07 11:26:10,461 : INFO : topic diff=0.320724, rho=0.451386
2022-05-07 11:26:10,469 : INFO : PROGRESS: pass 3, at document #2000/3816
2022-05-07 11:26:10,951 : INFO : merging changes from 2000 documents into a model of 3816 documents
2022-05-07 11:26:10,952 : INFO : topic #5 (0.100): 0.105*"diagnosis" + 0.068*"life" + 0.032*"time" + 0.028*"share" + 0.022*"lot" + 0.020*"spectrum" + 0.020*"experience" + 0.017*"research" + 0.017*"group" + 0.017*"self"
2022-05-07 11:26:10,953 : INFO : topic #1 (0.100): 0.080*"anxiety" + 0.035*"time" + 0.026*"mask" + 0.025*"kind" + 0.023*"lot" + 0.023*"talk" + 0.019*"voice" + 0.019*"tone" + 0.019*"sense" + 0.018*"life"
2022-05-07 11:26:10,953 : INFO : topic #4 (0.100): 0.060*"friend" + 0.041*"time" + 0.033*"life" + 0.028*"thing" + 0.027*"way" + 0.027*

2022-05-07 11:26:14,767 : INFO : topic diff=0.256346, rho=0.355604
2022-05-07 11:26:14,775 : INFO : PROGRESS: pass 6, at document #2000/3816
2022-05-07 11:26:15,213 : INFO : merging changes from 2000 documents into a model of 3816 documents
2022-05-07 11:26:15,214 : INFO : topic #4 (0.100): 0.082*"friend" + 0.041*"time" + 0.035*"therapy" + 0.034*"life" + 0.032*"group" + 0.030*"way" + 0.030*"thing" + 0.028*"lot" + 0.024*"therapist" + 0.018*"person"
2022-05-07 11:26:15,214 : INFO : topic #2 (0.100): 0.111*"time" + 0.041*"today" + 0.041*"thing" + 0.039*"work" + 0.035*"lot" + 0.031*"phone" + 0.025*"brain" + 0.021*"way" + 0.019*"day" + 0.019*"stuff"
2022-05-07 11:26:15,215 : INFO : topic #7 (0.100): 0.058*"life" + 0.054*"hair" + 0.037*"body" + 0.036*"adult" + 0.031*"woman" + 0.028*"childhood" + 0.027*"time" + 0.026*"kid" + 0.024*"daughter" + 0.023*"book"
2022-05-07 11:26:15,215 : INFO : topic #8 (0.100): 0.086*"day" + 0.073*"time" + 0.052*"work" + 0.041*"job" + 0.030*"home" + 0.027*"husband

2022-05-07 11:26:19,261 : INFO : merging changes from 2000 documents into a model of 3816 documents
2022-05-07 11:26:19,262 : INFO : topic #1 (0.100): 0.115*"anxiety" + 0.031*"depression" + 0.031*"mask" + 0.029*"lot" + 0.028*"time" + 0.025*"talk" + 0.024*"voice" + 0.023*"conversation" + 0.022*"tone" + 0.021*"kind"
2022-05-07 11:26:19,262 : INFO : topic #2 (0.100): 0.111*"time" + 0.043*"today" + 0.041*"thing" + 0.039*"work" + 0.034*"lot" + 0.033*"phone" + 0.029*"brain" + 0.022*"stuff" + 0.021*"way" + 0.019*"car"
2022-05-07 11:26:19,263 : INFO : topic #7 (0.100): 0.072*"life" + 0.051*"hair" + 0.043*"body" + 0.038*"adult" + 0.032*"woman" + 0.029*"kid" + 0.028*"child" + 0.027*"childhood" + 0.027*"time" + 0.026*"feeling"
2022-05-07 11:26:19,264 : INFO : topic #8 (0.100): 0.087*"day" + 0.076*"time" + 0.054*"work" + 0.045*"job" + 0.033*"home" + 0.027*"husband" + 0.026*"night" + 0.026*"house" + 0.025*"week" + 0.021*"morning"
2022-05-07 11:26:19,264 : INFO : topic #5 (0.100): 0.126*"diagnosis" 

In [52]:
lda.print_topics();

2022-05-07 11:26:20,210 : INFO : topic #0 (0.100): 0.078*"person" + 0.049*"family" + 0.030*"partner" + 0.030*"lot" + 0.028*"mom" + 0.027*"way" + 0.024*"help" + 0.023*"time" + 0.022*"thing" + 0.020*"relationship"
2022-05-07 11:26:20,212 : INFO : topic #1 (0.100): 0.119*"anxiety" + 0.032*"depression" + 0.030*"mask" + 0.030*"lot" + 0.027*"time" + 0.026*"talk" + 0.023*"conversation" + 0.023*"voice" + 0.023*"tone" + 0.020*"kind"
2022-05-07 11:26:20,213 : INFO : topic #2 (0.100): 0.110*"time" + 0.045*"today" + 0.040*"thing" + 0.039*"work" + 0.032*"phone" + 0.032*"lot" + 0.030*"brain" + 0.022*"way" + 0.021*"stuff" + 0.020*"car"
2022-05-07 11:26:20,214 : INFO : topic #3 (0.100): 0.060*"job" + 0.049*"way" + 0.032*"post" + 0.031*"work" + 0.026*"time" + 0.026*"life" + 0.025*"person" + 0.023*"community" + 0.022*"sense" + 0.018*"edit"
2022-05-07 11:26:20,215 : INFO : topic #4 (0.100): 0.091*"friend" + 0.042*"group" + 0.040*"time" + 0.039*"therapy" + 0.033*"life" + 0.033*"way" + 0.031*"thing" + 0.02

### Scattertext

In [53]:
autism_fem['category'] = 'fem'
autism_gen['category'] = 'gen'

In [54]:
merged_df = pd.concat([autism_fem, autism_gen], axis=0, join="inner")
merged_df.sample(10)

ID                                              title  \
1308  ny0jgb                          how i m feeling right now   
1435  swwvsv                  why are most nts so ignorant for    
610   u35ib5                til there are actually social rules   
1818  r3y2sp  the forehead is the conduit for love anyone el...   
1831  s8kn26                                      do you agree    
3815  q63li4  i m very tired of nt s thinking that autistic ...   
729   u0npok  do i remind any of you of yourselves or your c...   
254   ucnvoe  just unexpectedly received a day eviction noti...   
2603  ub64zu                 anyone else do the toe tuck thing    
3390  hckqar  at my last job i was discriminated against now...   

                    author         created_utc  score  upvote_ratio  \
1308          carefootable 2021-06-12 06:42:54    304          0.99   
1435           165cmgayboy 2022-02-20 08:48:12   1610          0.98   
610        lyinginthestars 2022-04-14 01:12:33    230          0.99   
1818         Mobypistachio 2021-11-28 06:45:11   1164          1.00   
1831  GlitteringMidnight98 2022-01-20 14:48:47   1148          0.97   
3815        screamingolive 2021-10-11 19:25:56    458          0.99   
729          Moonshine_113 2022-04-10 18:28:41     19          0.95   
254              heybabies 2022-04-26 21:58:37     60          0.94   
2603         HopefulDanger 2022-04-24 22:31:47     12          0.94   
3390            KeKitty127 2020-06-20 11:28:54    597          0.99   

                                               selftext       name  \
1308                                                     t3_ny0jgb   
1435                                                     t3_swwvsv   
610   for eighteen years of my life i ve lived such ...  t3_u35ib5   
1818                                                     t3_r3y2sp   
1831                                                     t3_s8kn26   
3815  at least for me i just show my empathy differe...  t3_q63li4   
729   hello i am year old girl who has been question...  t3_u0npok   
254   but i still have hours until i can break down ...  t3_ucnvoe   
2603  it s really weird and kinda hard to explain bu...  t3_ub64zu   
3390  i have been blatantly discriminated against wh...  t3_hckqar   

      num_comments                                          full_text  \
1308            22                         how i m feeling right now    
1435           137                 why are most nts so ignorant for     
610             76  til there are actually social rules for eighte...   
1818           118  the forehead is the conduit for love anyone el...   
1831           218                                     do you agree     
3815           146  i m very tired of nt s thinking that autistic ...   
729             18  do i remind any of you of yourselves or your c...   
254             10  just unexpectedly received a day eviction noti...   
2603            10  anyone else do the toe tuck thing  it s really...   
3390            40  at my last job i was discriminated against now...   

                                        full_text_nouns  sentiment_score  \
1308                                                              0.1280   
1435                                                             -0.4715   
610   til life i ignorance i i research autism i i s...           0.0636   
1818            forehead conduit love anyone affection            0.9081   
1831                                                              0.3612   
3815            s nt sociopath i sherlock brain person           -0.4787   
729   childhood behavior hello i year girl awhile au...           0.9842   
254   day eviction notice meltdown partner home care...          -0.5789   
2603  anyone toe thing bed blanket i front back blan...           0.0927   
3390  job i spergieness roommate coworker employer i...           0.8316   

     category  
1308      fem  
1435      gen  
610       fem  
1818      gen 

In [55]:
corpus = st.CorpusFromPandas(
    merged_df[:100],
    category_col = 'category',
    text_col = 'full_text',
    nlp=st.whitespace_nlp_with_sentences
).build()

In [56]:
html = st.produce_scattertext_explorer(
        corpus,
        category="fem",
        category_name='1',
        not_category_name='2',
        minimum_term_frequency=10,
        pmi_threshold_coefficient=5,
        width_in_pixels=1000,
        )


In [57]:
open('scattertext.html', 'wb').write(html.encode('utf-8'));

#### Doesn't look great.. I need to work to understand this better

# Stemming and Lemmatization
#### I ran out of time, here's a start to this work

In [58]:
wnl = WordNetLemmatizer()
stemmer = LancasterStemmer()
def lemmat(text):
    text = text.split(' ')
    for i, word in enumerate(text):
        text[i] = wnl.lemmatize(word)
    return ' '.join(text)


In [59]:
text = ' '.join(corpus_f)
lemmat(text)

'origin story megathread we get a lot of foot traffic from people who are in the process of discovering investigating and considering an autism diagnosis this is a very turbulent time and people going through this discovery process want to know if they are on the right track unfortunately we are not medical professional and we cannot give any advice on what individual people should or should not do however those of u who have gone through this process can still help by sharing our experience with it hopefully the new people will see a story in the comment that they resonate with so please tell u your origin story regale u with tale of how you discovered the world s most unusual superpower question we see lot are how did you first learn about the way autism present in girl when did you realize you fit on the spectrum what made you realize you were autistic is going after a diagnosis worth it what is the diagnosis process like  diagnostic resource megathread hi amazing aspergirls since t

# Future Work
- SpaCy for parts of speech tagging (NLTK had a lot of errors)
- Build cosine similarity matrix and, if there's time, a recommender system in my jupyter notebook using this
- Use CorEx to define topic categories before generating them